Define some required variables, parents, and functions:

In [ ]:
var('k t z')

In [ ]:
assume(k, 'integer')
PR_R = PolynomialRing(ZZ, "R").fraction_field()
R = PR_R("R")
AR.<n> = AsymptoticRing('QQ^n * n^QQ * log(n)^QQ', PR_R)

In [ ]:
AR_Z.<Z> = AsymptoticRing('Z^QQ * log(Z)^QQ', PR_R)
AR_T.<T> = AsymptoticRing('T^QQ * log(T)^QQ', SR.subring(accepting_variables=[k]))

In [ ]:
def upsilon(z):
    return (1 - sqrt(1 - 4*z))/(2*z) - 1
def chi(k):
    return 2*pi*I*k/log(2)

In [ ]:
zl = 1/4*(1-1/Z)
assert 1-4*zl == 1/Z

### Register Function

Generating function of binary trees with register function $\leq r$:

In [ ]:
def B(r, z):
    return (1 - upsilon(z)^2)/upsilon(z) * sum(upsilon(z)^(2^j)/(1 - upsilon(z)^(2^(j+1))) for j in srange(0, r+1))

Expansions for small values of $r$:

In [ ]:
B(0, z).taylor(z, 0, 20)

In [ ]:
B(1, z).taylor(z, 0, 20)

In [ ]:
B(2, z).taylor(z, 0, 20)

In [ ]:
B(3, z).taylor(z, 0, 20)

### Number of $r$-Branches

#### Theorem 1; Expectation

Generating function for the number of $r$-branches:

In [ ]:
def F1(z):
    return (1 - upsilon(z)^2)/(upsilon(z)) * upsilon(z)^(R)/(1 - upsilon(z)^(R))^2

Expansion for $z \to 1/4$

In [ ]:
expansion_F1 = F1(zl + O(1/Z^5))
expansion_F1.show()

Coefficient growth via singularity analysis:

In [ ]:
contribution_F1 = expansion_F1._singularity_analysis_('n', 1/4, precision=4).map_coefficients(expand)
contribution_F1.show()

In [ ]:
catalan_asy = asymptotic_expansions.Binomial_kn_over_n(n, 2, precision=5)/(n+1)
catalan_asy.show()

Asymptotic expansion of the expectation:

In [ ]:
E_nr = (contribution_F1 / catalan_asy).map_coefficients(lambda x: expand(SR(PR_R(x.expand()))))
E_nr.show()

#### Theorem 1, Variance

In [ ]:
def F2(z):
    return 2 * (1 - upsilon(z)^2)/(upsilon(z)) * upsilon(z)^(2*R)/(1 - upsilon(z)^(R))^4

Expansion for $z \to 1/4$:

In [ ]:
expansion_F2 = F2(zl + O(1/Z^5))
expansion_F2.show()

In [ ]:
E2_numerator = expansion_F2._singularity_analysis_('n', 1/4)
E2_nr = (E2_numerator / catalan_asy).map_coefficients(Expression.canonicalize_radical)
E2_nr.show()

Computation of the actual variance:

In [ ]:
V_nr = (E2_nr + E_nr - E_nr^2).map_coefficients(Expression.canonicalize_radical)
V_nr.show()

#### Theorem 3

In [ ]:
zetaderiv(1, RBF(-1))

Mellin transformation:

In [ ]:
M(s) = gamma(s) * zeta(s-1) / (1 - exp(-s*log(2)))

Residues everywhere except at $\chi_k$:

In [ ]:
residue_nonfluc = fast_callable((M(s)*t^-s).residue(s==0)
                                + (M(s)*t^-s).residue(s==2).simplify(), vars=[t])(1/T) + O(1/T^2)
residue_nonfluc.show()

Singular expansion for $F(z)$ at $z\to 1/4$, without residues from $\chi_k$:

In [ ]:
def left_factor(z):
    return (1 - upsilon(z)^2)/upsilon(z)
left_factor(zl + O(Z^-4))

In [ ]:
def t_in_z(z):
    return -log(upsilon(z))
t_in_z(zl + O(Z^-4))

In [ ]:
expansion_nonfluc = left_factor(zl+O(Z^-4)) * (
    residue_nonfluc.subs(T=1/t_in_z(zl+O(Z^-4)))).map_coefficients(lambda x: x.subs({log(1/2): -log(2)}))

In [ ]:
expansion_nonfluc.show()

In [ ]:
expectation_nonfluc = expansion_nonfluc._singularity_analysis_('n', 1/4, precision=3)/ catalan_asy
expectation_nonfluc = expectation_nonfluc.map_coefficients(expand)

In [ ]:
expectation_nonfluc.show()

For the fluctuation: the residue at $\chi_k$ is given as follows:

In [ ]:
residue_fluc_k = (M(s) * t^-s).residue(s==chi(k))
residue_fluc_k.show()

In [ ]:
expansion_fluc_k = left_factor(zl+O(Z^-2))*fast_callable(residue_fluc_k, vars=[t, k])(t_in_z(zl+O(Z^-2)), k)
expansion_fluc_k.show()

In [ ]:
contribution_fluc_k = expansion_fluc_k._singularity_analysis_('n', 1/4, precision=1)/catalan_asy
contribution_fluc_k.show()